In [18]:
!bash batch_train_data.sh

In [19]:
!cat train-data*.csv > models/20192009_14/train.csv

In [20]:
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import pickle
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [53]:
!cat models/20192009_14/train.csv | wc -l

   39746


In [22]:
!ls models/20192009_14/

train.csv


In [79]:
features = ["f" + str(i) for i in range(0,243)]
label = ["action"]

headers = features + label

df = pd.read_csv('models/20192009_14/train.csv', 
                 sep = ',', 
                 header = None,
                 names = headers)
df

f0  f1  f2  f3  f4  f5  f6  f7  f8  f9  ...  f234  f235  f236  f237  \
0      0   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
1      4   0   0   0   0   1   0   0   0   0  ...     0     0     0     0   
2      2   0   1   0   0   0   1   0   0   0  ...     0     0     0     0   
3      0   0   0   0   0   0   0   1   0   1  ...     0     0     0     0   
4      4   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
...   ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...   ...   ...   ...   ...   
3860   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3861   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3862   3   0   0   0   0   0   0   0   0   0  ...     0     0     0     0   
3863   3   0   0   0   0   0   0   0   1   0  ...     0     0     0     0   
3864   3   0   0   0   0   0   0   0   1   0  ...     0     0     0     0   

      f238  f239  f240  f241  f242  action  
0        0     0     0     0     0       0  
1        0     0     0     0     0       0  
2        0     0     0     0     0       0  
3        0     0     0     0     0       0  
4        0     0     0     0     0       4  
...    ...   ...   ...   ...   ...     ...  
3860     1     0     0     0     0       3  
3861     1     0     0     0     0       3  
3862     1     0     0     0     0       2  
3863     1     0     0     0     0       3  
3864     1     0     0     0     0       2  

[3865 rows x 244 columns]

In [55]:
print("headers length: {}, df lenght: {}".format(len(headers), len(df)))

headers length: 124, df lenght: 39746


In [56]:
df["f0"].value_counts()

2    9534
4    9342
0    9310
1    8904
3    1357
5    1299
Name: f0, dtype: int64

In [57]:
print("different actions count \n{}".format(df.drop_duplicates()['action'].value_counts()))

different actions count 
2    9895
3    6119
5    6007
0    5993
1    5353
4    5131
Name: action, dtype: int64


In [58]:
print("no of states without duplicates: {}".format(len(df.drop_duplicates())))

no of states without duplicates: 38498


In [59]:
y_train_all = df["action"]
X_train_all = df.drop(columns="action")

In [60]:
print("no of states without duplicates and action column: {}".format(len(X_train_all.drop_duplicates())))

no of states without duplicates and action column: 38458


In [30]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [31]:
# X_train_all[["f0", "f1"]]

In [81]:
def evaluate_model(xtrain, ytrain, xtest, ytest, model):
    y_pred_test = model.predict(xtest)
    y_pred_train = model.predict(xtrain)
    test_accuracy = accuracy_score(ytest, y_pred_test)
    train_accuracy = accuracy_score(ytrain, y_pred_train)
    print('Training accuracy: {0:.2f}, evaluation accuracy: {1:.2f}'.format(train_accuracy, test_accuracy))


Basic logisting regresion

In [82]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, test_size=0.2)

classifier = LogisticRegression().fit(X_train, y_train)

In [83]:
evaluate_model(X_train, y_train, X_test, y_test, classifier)

Training accuracy: 0.29, evaluation accuracy: 0.27


In [64]:
pickle.dump(classifier, open("ai_model_logit.pkl","wb"))

In [65]:
classifier = LogisticRegression().fit(X_train_all, y_train_all)

xgboost

In [66]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, 
                                                    test_size=0.2, random_state=7)

xgb_model = XGBClassifier(n_estimators=500).fit(X_train, y_train,eval_set = [[X_test, y_test]], verbose = 1)

[0]	validation_0-merror:0.506038
[1]	validation_0-merror:0.489308
[2]	validation_0-merror:0.493333
[3]	validation_0-merror:0.411698
[4]	validation_0-merror:0.372075
[5]	validation_0-merror:0.359874
[6]	validation_0-merror:0.361761
[7]	validation_0-merror:0.359371
[8]	validation_0-merror:0.358994
[9]	validation_0-merror:0.358742
[10]	validation_0-merror:0.359245
[11]	validation_0-merror:0.359245
[12]	validation_0-merror:0.359371
[13]	validation_0-merror:0.360126
[14]	validation_0-merror:0.360755
[15]	validation_0-merror:0.361384
[16]	validation_0-merror:0.361635
[17]	validation_0-merror:0.357233
[18]	validation_0-merror:0.357233
[19]	validation_0-merror:0.357233
[20]	validation_0-merror:0.361132
[21]	validation_0-merror:0.366667
[22]	validation_0-merror:0.363145
[23]	validation_0-merror:0.358868
[24]	validation_0-merror:0.357987
[25]	validation_0-merror:0.359245
[26]	validation_0-merror:0.358994
[27]	validation_0-merror:0.356101
[28]	validation_0-merror:0.358742
[29]	validation_0-merror

[239]	validation_0-merror:0.347296
[240]	validation_0-merror:0.347799
[241]	validation_0-merror:0.347547
[242]	validation_0-merror:0.347547
[243]	validation_0-merror:0.347925
[244]	validation_0-merror:0.347799
[245]	validation_0-merror:0.347799
[246]	validation_0-merror:0.347421
[247]	validation_0-merror:0.347547
[248]	validation_0-merror:0.347799
[249]	validation_0-merror:0.34805
[250]	validation_0-merror:0.348176
[251]	validation_0-merror:0.347925
[252]	validation_0-merror:0.34805
[253]	validation_0-merror:0.347925
[254]	validation_0-merror:0.347925
[255]	validation_0-merror:0.34805
[256]	validation_0-merror:0.348428
[257]	validation_0-merror:0.348176
[258]	validation_0-merror:0.348553
[259]	validation_0-merror:0.348553
[260]	validation_0-merror:0.348302
[261]	validation_0-merror:0.34805
[262]	validation_0-merror:0.347799
[263]	validation_0-merror:0.347547
[264]	validation_0-merror:0.347421
[265]	validation_0-merror:0.347673
[266]	validation_0-merror:0.347547
[267]	validation_0-merro

[474]	validation_0-merror:0.350314
[475]	validation_0-merror:0.350189
[476]	validation_0-merror:0.349937
[477]	validation_0-merror:0.350063
[478]	validation_0-merror:0.349937
[479]	validation_0-merror:0.350063
[480]	validation_0-merror:0.350189
[481]	validation_0-merror:0.350189
[482]	validation_0-merror:0.350189
[483]	validation_0-merror:0.350063
[484]	validation_0-merror:0.350566
[485]	validation_0-merror:0.35044
[486]	validation_0-merror:0.350314
[487]	validation_0-merror:0.350189
[488]	validation_0-merror:0.349308
[489]	validation_0-merror:0.349811
[490]	validation_0-merror:0.349686
[491]	validation_0-merror:0.349811
[492]	validation_0-merror:0.350063
[493]	validation_0-merror:0.35044
[494]	validation_0-merror:0.350566
[495]	validation_0-merror:0.350063
[496]	validation_0-merror:0.350189
[497]	validation_0-merror:0.350189
[498]	validation_0-merror:0.350566
[499]	validation_0-merror:0.350566


In [67]:
evaluate_model(X_train, y_train, X_test, y_test, xgb_model)

Training accuracy: 0.71, evaluation accuracy: 0.65


In [68]:
xgb_model = XGBClassifier(n_estimators=500).fit(X_train_all, y_train_all)

In [69]:
pickle.dump(xgb_model, open("ai_model_xgb.pkl","wb"))

random forest model

In [70]:
forest_model = RandomForestClassifier(random_state=1, n_estimators=100)
forest_model.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [71]:
evaluate_model(X_train, y_train, X_test, y_test, forest_model)

Training accuracy: 1.00, evaluation accuracy: 0.64


In [72]:
forest_model.fit(X_train_all, y_train_all)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [73]:
pickle.dump(forest_model, open("ai_model_forest.pkl","wb"))

In [74]:
# min_max_scaler = MinMaxScaler()
# np_scaled = min_max_scaler.fit_transform(df)
# df_normalized = pd.DataFrame(np_scaled)
# df_normalized.columns = feature_cols + ['Class']

In [75]:
# def make_crosses(X_train, X_validation, degree=2):
#   from sklearn.preprocessing import PolynomialFeatures
#   poly = PolynomialFeatures(degree=degree)
#   X_train_poly = poly.fit_transform(X_train)
#   X_validation_poly = poly.transform(X_validation)
#   return X_train_poly, X_validation_poly

In [76]:
mlp_model = MLPClassifier(solver='adam', alpha=1e-5, 
                    hidden_layer_sizes=(60, 24, 24), 
                          random_state=1, verbose=True)

mlp_model.fit(X_train, y_train)

Iteration 1, loss = 1.69523565
Iteration 2, loss = 1.07814971
Iteration 3, loss = 0.90031100
Iteration 4, loss = 0.85833050
Iteration 5, loss = 0.82804405
Iteration 6, loss = 0.79795039
Iteration 7, loss = 0.77158373
Iteration 8, loss = 0.75531540
Iteration 9, loss = 0.73938735
Iteration 10, loss = 0.73114434
Iteration 11, loss = 0.72398349
Iteration 12, loss = 0.71579087
Iteration 13, loss = 0.70959806
Iteration 14, loss = 0.70549885
Iteration 15, loss = 0.69810609
Iteration 16, loss = 0.69388419
Iteration 17, loss = 0.68891574
Iteration 18, loss = 0.68532951
Iteration 19, loss = 0.68288483
Iteration 20, loss = 0.67542767
Iteration 21, loss = 0.67263534
Iteration 22, loss = 0.66910197
Iteration 23, loss = 0.66626042
Iteration 24, loss = 0.66199150
Iteration 25, loss = 0.66000305
Iteration 26, loss = 0.65384523
Iteration 27, loss = 0.65021331
Iteration 28, loss = 0.65062443
Iteration 29, loss = 0.64521922
Iteration 30, loss = 0.64319919
Iteration 31, loss = 0.63842710
Iteration 32, los

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(60, 24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='adam', tol=0.0001,
              validation_fraction=0.1, verbose=True, warm_start=False)

In [77]:
evaluate_model(X_train, y_train, X_test, y_test, mlp_model)

Training accuracy: 0.79, evaluation accuracy: 0.62


In [78]:
mlp_model = MLPClassifier(solver='adam', alpha=1e-5, 
                    hidden_layer_sizes=(24, 24, 24), 
                          random_state=1, verbose=True, max_iter=1000)

mlp_model.fit(X_train_all, y_train_all)

Iteration 1, loss = 1.71745914
Iteration 2, loss = 1.14889255
Iteration 3, loss = 0.90411294
Iteration 4, loss = 0.83486245
Iteration 5, loss = 0.79585969
Iteration 6, loss = 0.77651207
Iteration 7, loss = 0.76528551
Iteration 8, loss = 0.75851234
Iteration 9, loss = 0.75256132
Iteration 10, loss = 0.74926267
Iteration 11, loss = 0.74460189
Iteration 12, loss = 0.74157233
Iteration 13, loss = 0.73868462
Iteration 14, loss = 0.73604049
Iteration 15, loss = 0.73279735
Iteration 16, loss = 0.73133653
Iteration 17, loss = 0.72846683
Iteration 18, loss = 0.72713480
Iteration 19, loss = 0.72511676
Iteration 20, loss = 0.72357778
Iteration 21, loss = 0.72338753
Iteration 22, loss = 0.72040294
Iteration 23, loss = 0.72034744
Iteration 24, loss = 0.71874376
Iteration 25, loss = 0.71781603
Iteration 26, loss = 0.71418056
Iteration 27, loss = 0.71352861
Iteration 28, loss = 0.71220809
Iteration 29, loss = 0.71217609
Iteration 30, loss = 0.71051924
Iteration 31, loss = 0.70837224
Iteration 32, los

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(24, 24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=1000, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='adam', tol=0.0001,
              validation_fraction=0.1, verbose=True, warm_start=False)

Save models to pkl

In [79]:
pickle.dump(mlp_model, open("ai_model_mlp.pkl","wb"))

In [80]:
!bash evaluate-ai.sh

evaluation of logit
evaluation logit with 10 attempts, resulted with, avg time: 9,95 and avg score: 19,85
evaluation of xgb
evaluation xgb with 10 attempts, resulted with, avg time: 6,3 and avg score: 13,3
evaluation of mlp
evaluation mlp with 10 attempts, resulted with, avg time: 9,1375 and avg score: 23,5
evaluation of forest
evaluation forest with 10 attempts, resulted with, avg time: 17,75 and avg score: 7,65


In [ ]:
# model_p = pickle.load(open("ai_model.pkl","rb"))
game_state_4f = (np.array([8,280,630,-1,1,674,-3,7,667,-1,2,649,-3,2,662,0,3,662,-1,4,655,-1,5,608,2,7,1,8,288,630,-1,1,672,-3,7,668,-1,2,650,-3,2,661,0,3,657,-1,4,649,-1,5,602,2,7,1,8,296,629,-1,1,670,-3,7,669,-1,2,651,-3,2,660,0,3,651,-1,4,643,-1,5,596,2,7,1,8,296,628,-1,1,665,-3,7,667,-1,2,650,-3,2,658,0,3,647,-1,4,638,-1,5,589,2,7])
                 .reshape(1, -1))

game_state_1f = (np.array([25, -410, 308, 5, 1, -343, 483, 1, 2, -417, 592, 5, 2, -184, 589, 1, 2, -222, 275, 7, 2, -93, 143, 3, -2, -128, 549, 1, -3, -121, 399, 6, -3]).reshape(1, -1))

xgb_model.predict(game_state_1f)